In [1]:
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.geom2d import CSG2d, Rectangle, Circle
from netgen.geom2d import SplineGeometry
from netgen.occ import *
import numpy as np

# Neumman Scatterer

In [90]:
scatterer = MoveTo(-0.2, 0).Rectangle(0.4, 0.05).Face()
scatterer.edges.name = 'scat'

outer = Circle((0,0), 0.5).Face()
inner = Circle((0,0), 0.4).Face()

bpf = Circle((0,0), 0.35).Face()
bpf.faces.name = 'inner'

pmlregion = outer - inner
pmlregion.faces.name = 'pml'
pmlregion.edges.name = 'pmlbnd'

bpfregion = inner - bpf
bpfregion.faces.name ='bpf'
bpfregion.edges.Min(X).name="bpfinner"
bpfregion.edges.Max(X).name="bpfouter"


simulation_domain = Glue([pmlregion, bpfregion, bpf])
geo = OCCGeometry(simulation_domain-scatterer, dim=2)

freq = 2000
c0 = 343
rho0= 1.21

mesh = Mesh(geo.GenerateMesh (maxh=c0/freq/12, minh=c0/freq/120))
mesh.Curve(3)

pml_ = mesh.SetPML(pml.Radial(rad=0.4,alpha=1j,origin=(0,0)), "pml")
print (mesh.GetMaterials(), mesh.GetBoundaries())


('pml', 'bpf', 'inner') ('pmlbnd', 'bpfouter', 'bpfinner', 'scat', 'scat', 'scat', 'scat')


# No Scatterer

In [71]:
outer = Circle((0,0), 0.5).Face()
inner = Circle((0,0), 0.4).Face()

bpf = Circle((0,0), 0.35).Face()
bpf.faces.name = 'inner'

pmlregion = outer - inner
pmlregion.faces.name = 'pml'
pmlregion.edges.name = 'pmlbnd'

bpfregion = inner - bpf
bpfregion.faces.name ='bpf'
bpfregion.edges.Min(X).name="bpfinner"
bpfregion.edges.Max(X).name="bpfouter"


simulation_domain = Glue([pmlregion, bpfregion, bpf])
geo = OCCGeometry(simulation_domain, dim=2)

freq = 2000
c0 = 343
rho0= 1.21

mesh = Mesh(geo.GenerateMesh (maxh=c0/freq/12, minh=c0/freq/120))
mesh.Curve(3)

pml_ = mesh.SetPML(pml.Radial(rad=0.4,alpha=1j,origin=(0,0)), "pml")
print (mesh.GetMaterials(), mesh.GetBoundaries())


('pml', 'bpf', 'inner') ('pmlbnd', 'bpfouter', 'bpfinner')


# Simulation

In [91]:
omega = 2*np.pi*freq
iomega = 1j * omega
k = omega / c0
ik = iomega / c0
delta = 1 / (omega**2)

pw_direction = CoefficientFunction((0, -1))  # Direction of the plane wave
u_inc = exp(-1j * k * (pw_direction[0]*x + pw_direction[1]*y))

order = 5
fes = Compress(H1(mesh, complex=True, order=order, dirichlet="pmlbnd"))
feslam = Compress(H1(mesh,complex=True, order=order, definedon=mesh.Boundaries("bpfinner")))


bdry_values = {'bpf': u_inc}
cf = mesh.MaterialCF(bdry_values, default=0)
u_inc_cf = GridFunction(fes, name='bdry')
u_inc_cf.Set(cf, definedon = mesh.Materials("bpf"))

grad_u_inc_cf = -1j * k * pw_direction * u_inc_cf

Draw(u_inc_cf,mesh)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene

In [92]:
n = specialcf.normal(2)
h = specialcf.mesh_size


a = BilinearForm(fes)
f = LinearForm(fes)
b = BilinearForm(trialspace=fes, testspace=feslam)

u,v = fes.TnT()
uhat,vhat = feslam.TnT()

a += -grad(u)*grad(v)*(delta/rho0)*dx - ik**2*u*v*(delta/rho0)*dx
a += 1j*k*u*v*ds("pmlbnd")


b += (((u+u_inc_cf) - uhat) - ((v+u_inc_cf))) * dx(definedon = mesh.Boundaries("bpfinner"))


gfu = GridFunction(fes)
gfu_inc = GridFunction(fes)
gfu_rhs = GridFunction(fes)

f += -(delta) * grad_u_inc_cf * n * v *ds(definedon = mesh.Boundaries("bpfouter"))

r = u_inc_cf.vec.CreateVector()

with TaskManager():
    a.Assemble()
    f.Assemble()
    r.data = a.mat * u_inc_cf.vec + f.vec
    # r.data = f.vec
    gfu.vec.data = a.mat.Inverse(fes.FreeDofs()) * r
    gfu_inc.vec.data = r

Draw(gfu, mesh, "scattered")

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene

In [93]:
from ngsolve.krylovspace import CGSolver, GMRes

with TaskManager():
    a.Assemble()
    b.Assemble()
    f.Assemble()
    r.data = -a.mat * u_inc_cf.vec + f.vec
    # r.data = f.vec
    ainv = a.mat.Inverse(inverse="sparsecholesky", freedofs=fes.FreeDofs())
    S = b.mat @ ainv @ b.mat.T
    g = (b.mat @ ainv * r).Evaluate()
    invS = CGSolver(S, pre=IdentityMatrix(feslam.ndof), printrates="\r", maxiter=1000, atol=1e-8)
    lam = g.CreateVector()
    lam.data = invS * g
    r_lam = (r - b.mat.T * lam)
    gfu.vec.data = ainv * r_lam
    gfu_inc.vec.data = u_inc_cf.vec
    gfu_rhs.vec.data = r


Draw(gfu, mesh);
Draw(gfu_rhs, mesh);


CG converged in 502 iterations to residual 7.205087210514587e-09


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…